## Домашнее задание (см. после слов "ДЗ")

Основаная задача - **построить хорошую тематическую модель с интерпретируемыми топиками с помощью LDA в gensim и NMF в sklearn**.


1) сделайте нормализацию (если pymorphy2 работает долго используйте mystem или попробуйте установить быструю версию - `pip install pymorphy2[fast]`, можно использовать какой-то другой токенизатор); 

2) добавьте нграммы (в тетрадке есть закомменченая ячейка с Phrases,  можно также попробовать другие способы построить нграммы); 

3) сделайте хороший словарь (отфильтруйте слишком частотные и редкие слова, попробуйте удалить стоп-слова); 

4) постройте несколько LDA моделей (переберите количество тем, можете поменять eta, alpha, passes), если получаются плохие темы, поработайте дополнительно над предобработкой и словарем; 

5) для самой хорошей модели в отдельной ячейке напечатайте 3 хороших (на ваш вкус) темы;

6) между словарем и обучением модели добавьте tfidf (`gensim.models.TfidfModel(corpus, id2word=dictionary); corpus = tfidf[corpus]`);

7) повторите пункт 4 на преобразованном корпусе;

8) в отдельной ячейке опишите как изменилась модель (приведите несколько тем, которые стали лучше или хуже, или которых раньше вообще не было; можно привести значения перплексии и когерентности для обеих моделей)

9) проделайте такие же действия для NMF (образец в конце тетрадки), для построения словаря воспользуйтесь возможностями Count или Tfidf Vectorizer (попробуйте другие значение max_features, min_df, max_df, сделайте нграмы через ngram_range, если хватает памяти), попробуйте такие же количества тем

10) в отдельной ячейки напечатайте таблицу с темами лучшей NMF модели, сравните их с теми, что получились в LDA.

Сохраните тетрадку с экспериментами и положите её на гитхаб, ссылку на неё укажите в форме.

**Оцениваться будут главным образом пункты 5, 8 и 10. (2, 3, 2 баллов соответственно). Чтобы заработать остальные 3 балла, нужно хотя бы немного изменить мой код на промежуточных этапах (добавить что-то, указать другие параметры и т.д). **

In [1]:
import gensim
import json
import re
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from pymorphy2 import MorphAnalyzer
import pyLDAvis.gensim
import string
from collections import Counter
import warnings
warnings.filterwarnings("ignore")

morph = MorphAnalyzer()

## Данные

In [2]:
stops = set(stopwords.words('russian')) | {'gt',}
def remove_tags(text):
    return re.sub(r'<[^>]+>', '', text)

def normalize(words):
    norm_words = [morph.parse(word)[0].normal_form for word in words if len(set(word)) > 1]
    return norm_words

def opt_normalize(texts, top=None):
    uniq = Counter()
    for text in texts:
        uniq.update(text)
    
    norm_uniq = {word:morph.parse(word)[0].normal_form for word, _ in uniq.most_common(top)}
    
    norm_texts = []
    for text in texts:
        
        norm_words = [norm_uniq.get(word) for word in text]
        norm_words = [word for word in norm_words if word and word not in stops]
        norm_texts.append(norm_words)
        
    return norm_texts

def tokenize(text):
    words = [word.strip(string.punctuation) for word in text.split()]
    words = [word for word in words if word]
    
    return words

Возьмем 4 тыс статьи с Хабра. Это мало для хорошей тематической модели, но иначе у нас просто ничего не обучится за семинар.

In [3]:
texts = open('habr_texts.txt').read().splitlines()

In [4]:
f = open('habr_texts.vw', 'w')

for i, text in enumerate(texts):
    c = Counter(text)
    doc = 'doc_'+ str(i) + ' '
    vw_text = ' '.join([x+':'+str(c[x]) for x in c])
    
    f.write(doc + vw_text  + '\n')
f.close()

В текстах есть тэги. Потрем их. Ещё токенизируем самым простым способом и нормализуем Pymorphy.

In [306]:
texts = open('habr_texts.txt').read().splitlines()
texts = [tokenize(remove_tags(text.lower())) for text in texts]

In [307]:
texts = open('habr_texts.txt').read().splitlines()
texts = [normalize(tokenize(text.lower())) for text in texts]

In [308]:
texts = open('habr_texts.txt').read().splitlines()
texts = opt_normalize([tokenize(remove_tags(text.lower())) for text in texts], 30000)

In [309]:
texts[0][:10]

['это',
 'open',
 'source',
 'библиотека',
 'разработать',
 'язык',
 'c',
 'net',
 'платформа',
 'работа']

In [310]:
# для нграммов
# ph = gensim.models.Phrases(texts, scoring='npmi', threshold=0.4) # threshold можно подбирать
# p = gensim.models.phrases.Phraser(ph)
# ngrammed_texts = p[texts]

### Тематическое моделирование в gensim

Для моделей нужно сделать словарь.

In [311]:
dictinary = gensim.corpora.Dictionary(texts)

In [312]:
dictinary.filter_extremes(no_above=0.3)
dictinary.compactify()

In [313]:
print(dictinary)

Dictionary(12255 unique tokens: ['2-х', '3.0', 'address', 'api', 'architecture']...)


Преобразуем наши тексты в мешки слов. 

In [314]:
corpus = [dictinary.doc2bow(text) for text in texts]
# если текстов много, то тут может быть генератор

In [315]:
lda = gensim.models.LdaMulticore(corpus, id2word=dictinary, passes=5, eta='auto', iterations=10) # если поддерживается многопоточность

Посмотрим на топики.

In [15]:
lda.print_topics()

[(27,
  '0.008*"компонент" + 0.008*"элемент" + 0.006*"состояние" + 0.006*"чд" + 0.004*"хокинг" + 0.004*"return" + 0.004*"объект" + 0.004*"метод" + 0.003*"класс" + 0.003*"const"'),
 (34,
  '0.006*"игра" + 0.003*"плата" + 0.003*"камера" + 0.002*"корпус" + 0.002*"процессор" + 0.002*"какой-то" + 0.002*"сеть" + 0.002*"модуль" + 0.002*"модель" + 0.002*"конец"'),
 (70,
  '0.007*"датчик" + 0.005*"ток" + 0.004*"напряжение" + 0.003*"значение" + 0.003*"температура" + 0.003*"схема" + 0.003*"устройство" + 0.003*"параметр" + 0.002*"питание" + 0.002*"google"'),
 (21,
  '0.090*"up" + 0.027*"days" + 0.020*"6" + 0.010*"down" + 0.008*"scrum" + 0.006*"устройство" + 0.005*"продукт" + 0.004*"active" + 0.003*"connection" + 0.003*"closed"'),
 (76,
  '0.017*"user" + 0.016*"do" + 0.015*"conn" + 0.014*"end" + 0.012*"post" + 0.010*"тест" + 0.010*"test" + 0.009*"файл" + 0.008*"0.0" + 0.007*"assert"'),
 (6,
  '0.010*"файл" + 0.010*"модуль" + 0.006*"метод" + 0.005*"windows" + 0.005*"компонент" + 0.005*"linux" + 0.00

Ещё есть штука для визуализации.

In [16]:
pyLDAvis.enable_notebook()

In [17]:
pyLDAvis.gensim.prepare(lda, corpus, dictinary)

PreparedData(topic_coordinates=           Freq  cluster  topics         x         y
topic                                               
39     5.829475        1       1 -0.122331  0.031636
7      4.755463        1       2 -0.111012 -0.021131
10     3.988786        1       3 -0.131166 -0.030374
84     3.944776        1       4 -0.068022  0.066901
49     3.643156        1       5 -0.123092 -0.098174
94     3.469025        1       6  0.201410 -0.058787
2      3.354572        1       7 -0.050408  0.035927
8      3.221645        1       8  0.174078 -0.041054
58     2.590413        1       9 -0.068136  0.021167
37     2.516033        1      10  0.136152  0.057620
86     2.293237        1      11 -0.100089 -0.027274
68     2.243282        1      12 -0.027247  0.051473
0      2.210210        1      13  0.160738 -0.003833
72     2.209647        1      14 -0.113983 -0.057510
52     1.951346        1      15 -0.025753 -0.088510
97     1.922918        1      16 -0.115530  0.008074
95     1.853106        1      17  0.100438  0.018965
73     1.740446        1      18 -0.085046 -0.013335
93     1.730917        1      19  0.108086 -0.051408
1      1.730749        1      20  0.087339  0.009817
41     1.698364        1      21  0.087725 -0.017348
6      1.542162        1      22  0.054529  0.039957
89     1.501250        1      23 -0.059657  0.053697
85     1.478736        1      24 -0.053403  0.036495
99     1.394136        1      25  0.076696 -0.012067
48     1.389069        1      26 -0.082028  0.010632
44     1.371451        1      27 -0.104257 -0.023531
28     1.311000        1      28  0.038870  0.045320
32     1.282632        1      29 -0.077844  0.042398
61     1.201493        1      30  0.048820  0.064402
...         ...      ...     ...       ...       ...
30     0.265219        1      71  0.007522 -0.005258
43     0.263204        1      72  0.000544 -0.006408
79     0.232253        1      73  0.046607 -0.012680
81     0.226533        1      74  0.024401 -0.015620
54     0.224894        1      75  0.025663 -0.001219
17     0.199108        1      76 -0.010080  0.003326
4      0.190941        1      77  0.006625  0.003346
29     0.189181        1      78 -0.034213 -0.004523
74     0.177563        1      79 -0.011779  0.010815
77     0.166018        1      80 -0.005889  0.011880
53     0.165916        1      81  0.017487 -0.007927
38     0.156684        1      82 -0.011146  0.013635
56     0.133372        1      83  0.016937 -0.014179
18     0.128111        1      84  0.022859 -0.031344
40     0.125673        1      85 -0.012504  0.004922
64     0.121816        1      86 -0.012311 -0.006580
66     0.114343        1      87 -0.023020 -0.012462
51     0.113149        1      88 -0.010168  0.008123
90     0.104836        1      89  0.035293 -0.004662
23     0.104572        1      90 -0.013474 -0.015324
92     0.098425        1      91 -0.033261 -0.018920
27     0.098071        1      92  0.027843 -0.038795
46     0.092441        1      93  0.007523  0.000567
75     0.062193        1      94  0.000889 -0.004152
65     0.060802        1      95  0.007158  0.004999
33     0.044274        1      96  0.008765 -0.004577
88     0.042456        1      97 -0.013231 -0.003644
82     0.036593        1      98  0.014595  0.001517
59     0.036581        1      99  0.010794  0.001850
20     0.014191        1     100  0.012357 -0.007833

[100 rows x 5 columns], topic_info=      Category         Freq                Term        Total  loglift  logprob
term                                                                          
377    Default  5731.000000                игра  5731.000000  30.0000  30.0000
538    Default  6236.000000                   0  6236.000000  29.0000  29.0000
1141   Default  5211.000000                файл  5211.000000  28.0000  28.0000
34     Default  4523.000000                  if  4523.000000  27.0000  27.0000
1674   Default  5047.000000          устройство  5047.000000  26.0000  26.0000
61     Default  4132.000000              

Можно посмотреть метрики.

In [18]:
import numpy as np

In [20]:
lda.log_perplexity(corpus[:2000], total_docs=100)

-27.785399207546

In [21]:
coherence_model_lda = gensim.models.CoherenceModel(model=lda, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [22]:
topics = []
for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

In [23]:
coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [24]:
coherence_model_lda.get_coherence()

0.4778247703816194

### Разложение матриц в sklearn

In [25]:
from sklearn.decomposition import NMF
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
import pandas as pd

Sklearn принимает на вход строки, поэтому склеим наши списки.

In [26]:
stexts = [' '.join(text) for text in texts]

Сделаем матрицу слова-документы с помощью TfidfVectorizer

In [27]:
vectorizer = TfidfVectorizer(max_features=25000, min_df=5, max_df=0.3, lowercase=False)
X = vectorizer.fit_transform(stexts)

Разложим её.

In [28]:
model = NMF(n_components=30)

In [29]:
model.fit(X)

NMF(alpha=0.0, beta_loss='frobenius', init=None, l1_ratio=0.0, max_iter=200,
  n_components=30, random_state=None, shuffle=False, solver='cd',
  tol=0.0001, verbose=0)

In [30]:
def get_nmf_topics(model, n_top_words):
    
    #id слов.
    feat_names = vectorizer.get_feature_names()
    
    word_dict = {};
    for i in range(30):
        
        #топ n слов для темы.
        words_ids = model.components_[i].argsort()[:-n_top_words - 1:-1]
        words = [feat_names[key] for key in words_ids]
        word_dict['Topic # ' + '{:02d}'.format(i+1)] = words;
    
    return pd.DataFrame(word_dict);

In [31]:
get_nmf_topics(model, 10)

Topic # 01 Topic # 02 Topic # 03   Topic # 04    Topic # 05   Topic # 06  \
0      объект     public       игра  космический    устройство      продукт   
1    значение       void      игрок      спутник      смартфон    сотрудник   
2        язык        new    игровой       орбита       телефон  программист   
3     элемент     string     играть       ракета   аккумулятор       клиент   
4       метод    private   персонаж         марс          сеть         опыт   
5       класс     return      steam      аппарат        датчик       бизнес   
6  переменный      class         vr        земля     мобильный         идея   
7      строка     static      unity      станция       батарея     заказчик   
8        блок      класс   геймплей         наса  беспроводный       деньга   
9    алгоритм        var       жанр         луна         умный     понимать   

  Topic # 07  Topic # 08 Topic # 09     Topic # 10      ...        Topic # 21  \
0         lt       товар        the             ия      ...              сайт   
1         gt      скидка         to       обучение      ...          страница   
2        div        цена         of      нейросеть      ...           реклама   
3     return     магазин        and           сеть      ...           браузер   
4      const  покупатель         in      интеллект      ...           контент   
5  компонент     покупка         is       машинный      ...         рекламный   
6      input  распродажа         on  искусственный      ...            клиент   
7        int     продажа        for      нейронный      ...             домен   
8        std     пятница        you       алгоритм      ...            трафик   
9      class    продавец       from    изображение      ...        посетитель   

   Topic # 22 Topic # 23  Topic # 24   Topic # 25   Topic # 26 Topic # 27  \
0        файл         if         бот      windows       камера       звук   
1       папка     return   сообщение    microsoft        видео     сигнал   
2      скрипт       else    telegram        linux     движение    наушник   
3      строка        end         чат       studio  изображение    частота   
4       пакет        amp       канал        azure     смартфон  усилитель   
5      модуль        var    телеграм       visual         кадр   звуковой   
6  директория        int  мессенджер          net  регистратор  искажение   
7        sudo   function         api       server   фотография     музыка   
8      сборка       true      сервис  виртуальный     blackvue   диапазон   
9   настройка      false         bot   обновление   разрешение      волна   

  Topic # 28     Topic # 29     Topic # 30  
0    android          атака          робот  
1     google   безопасность     автомобиль  
2  мобильный     уязвимость        ребёнок  
3        ios  злоумышленник         машина  
4        app         пароль  робототехника  
5       play         защита    беспилотный  
6      apple    вредоносный           lego  
7      swift         доступ         датчик  
8   firebase           ключ       движение  
9        api     шифрование       скорость  

[10 rows x 30 columns]

## ДЗ

**Немного изменим предобработку текстов (воспользуемся `mystem` и удалим "мусор")**

In [316]:
from string import punctuation
from pymystem3 import Mystem

In [317]:
russian_stopwords = set(stopwords.words('russian')) | {'gt',} | {'lt',} # lt встречается очень часто

In [318]:
punct = punctuation + '«»—…“”*№–'
mystem = Mystem()

In [319]:
def preprocessing(text):
    text = re.sub('\s{2,}', '', text)
    regex = re.compile('[^a-zA-ZА-Яа-я]') # );\t}\t -- достаточно много подобных сочетаний различных символов
    text = regex.sub(' ', text)
    tokens = mystem.lemmatize(text)
    tokens = [token for token in tokens if token not in russian_stopwords \
              and token != ' '  \
              and token.strip() not in punct \
              and len(token) > 1]
    
    return tokens

In [320]:
texts = open('habr_texts.txt').read().splitlines()

In [321]:
texts = [preprocessing(remove_tags(text.lower())) for text in texts]

In [322]:
dictinary = gensim.corpora.Dictionary(texts)

In [323]:
dictinary.filter_extremes(no_above=0.3)
dictinary.compactify()

In [324]:
corpus = [dictinary.doc2bow(text) for text in texts]

In [325]:
lda = gensim.models.LdaMulticore(corpus, id2word=dictinary, passes=5, eta='auto', iterations=10) # если поддерживается многопоточность

In [326]:
lda.log_perplexity(corpus, total_docs=100)

-30.963653596602548

In [327]:
coherence_model_lda = gensim.models.CoherenceModel(model=lda, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [328]:
topics = []
for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

In [329]:
coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [114]:
coherence_model_lda.get_coherence()

0.5062408651662066

**н-граммы**

In [152]:
# для нграммов
ph = gensim.models.Phrases(texts, scoring='npmi', threshold=0.4) # threshold можно подбирать
p = gensim.models.phrases.Phraser(ph)
ngrammed_texts = p[texts]

In [153]:
dictinary = gensim.corpora.Dictionary(ngrammed_texts)

In [154]:
dictinary.filter_extremes(no_above=0.3)
dictinary.compactify()

In [155]:
corpus = [dictinary.doc2bow(text) for text in ngrammed_texts]

In [156]:
%%time
lda = gensim.models.LdaMulticore(corpus, id2word=dictinary, passes=5, eta='auto', iterations=10) # если поддерживается многопоточность

CPU times: user 52.7 s, sys: 11.1 s, total: 1min 3s
Wall time: 1min 1s


In [157]:
lda.log_perplexity(corpus, total_docs=100)

-34.51317598446855

In [162]:
coherence_model_lda = gensim.models.CoherenceModel(model=lda, 
                                                   texts=ngrammed_texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [163]:
topics = []
for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

In [164]:
coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=ngrammed_texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [165]:
coherence_model_lda.get_coherence()

0.4681731407388889

**Частотность**

In [172]:
cnt = Counter()
for text in texts:
    for word in text:
        cnt[word] += 1

In [226]:
dictinary = gensim.corpora.Dictionary(texts)

In [227]:
# dictinary.filter_extremes(no_below=1000)
dictinary.filter_extremes(no_above=50)
dictinary.compactify()

In [228]:
corpus = [dictinary.doc2bow(text) for text in texts]

In [229]:
lda = gensim.models.LdaMulticore(corpus, id2word=dictinary, passes=5, eta='auto', iterations=10) # если поддерживается многопоточность

In [230]:
lda.log_perplexity(corpus, total_docs=100)

-26.475876277814436

In [231]:
coherence_model_lda = gensim.models.CoherenceModel(model=lda, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [232]:
topics = []
for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

In [233]:
coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [234]:
coherence_model_lda.get_coherence()

0.42451423017374496

**Перебор параметров**

In [276]:
dictinary = gensim.corpora.Dictionary(texts)

In [277]:
dictinary.filter_extremes(no_above=0.3)
dictinary.compactify()

In [278]:
corpus = [dictinary.doc2bow(text) for text in texts]

In [241]:
eta = ['auto', 1e-5, 1e-3, 0.1]
num_topics = [10, 20, 50, 100]

In [242]:
import itertools

In [243]:
for e, n in itertools.product(eta, num_topics):
    print('eta=%s, num_topics=%s' % (e, n))
    lda = gensim.models.LdaMulticore(corpus, num_topics=n, id2word=dictinary, passes=5, eta=e, iterations=10) # если поддерживается многопоточность
    print(lda.log_perplexity(corpus, total_docs=100))
    coherence_model_lda = gensim.models.CoherenceModel(model=lda, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')
    topics = []
    for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
        topic = [word for word, _ in topic]
        topics.append(topic)
    
    coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')
    print(coherence_model_lda.get_coherence())

eta=auto, num_topics=10
-12.553720225974242
0.43688409630416747
eta=auto, num_topics=20
-15.362930364072795
0.4960976025872064
eta=auto, num_topics=50
-22.11097445612409
0.4984942440153801
eta=auto, num_topics=100
-31.12896426336915
0.5149285387355866
eta=1e-05, num_topics=10
-47.339321305659226
0.475963099571759
eta=1e-05, num_topics=20
-80.87722703558339
0.47895972382780727
eta=1e-05, num_topics=50
-169.4228051362763
0.5066722052078596
eta=1e-05, num_topics=100
-294.70694691932414
0.4902435286605958
eta=0.001, num_topics=10
-30.00552207429334
0.46330908031823964
eta=0.001, num_topics=20
-46.8772398981959
0.47323304078773915
eta=0.001, num_topics=50
-84.05071751201875
0.4885753629828955
eta=0.001, num_topics=100
-126.2460590450104
0.4781637499739648
eta=0.1, num_topics=10
-14.912700778535902
0.4381459992535353
eta=0.1, num_topics=20
-18.420948246272122
0.5038251937902497
eta=0.1, num_topics=50
-24.03577070888016
0.48028361502816
eta=0.1, num_topics=100
-28.63561284726989
0.50134070658

`eta=auto, num_topics=100` + увеличим значение `passes`

In [279]:
lda = gensim.models.LdaMulticore(corpus, num_topics=100, id2word=dictinary, passes=25, eta='auto', iterations=10) # если поддерживается многопоточность
print(lda.log_perplexity(corpus, total_docs=100))

coherence_model_lda = gensim.models.CoherenceModel(model=lda, 
                                               texts=texts, 
                                               dictionary=dictinary, coherence='c_v')
topics = []
for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                               texts=texts, 
                                               dictionary=dictinary, coherence='c_v')
print(coherence_model_lda.get_coherence())

-18.401202613582292
0.5629665843644511


In [285]:
o, tw, th = topics[84], topics[48], topics[34]

In [286]:
topics_df = pd.DataFrame([o, tw, th], index=['тема1', 'тема2', 'тема3'])

In [287]:
topics_df

0            1         2            3            4      5  \
тема1       письмо        почта  рассылка        email  электронный   mail   
тема2       доклад  конференция      тема  выступление           ru  видео   
тема3  космический      спутник    орбита       ракета      аппарат   марс   

                 6            7            8          9  
тема1     почтовый        адрес  отправитель  сообщение  
тема2  мероприятие  презентация       спикер      слайд  
тема3        земля      корабль    двигатель       луна

**TF-IDF на лучших параметрах**

In [245]:
tfidf = gensim.models.TfidfModel(corpus, id2word=dictinary)
corpus = tfidf[corpus]

In [246]:
lda = gensim.models.LdaMulticore(corpus, num_topics=100, id2word=dictinary, passes=25, eta='auto', iterations=10) # если поддерживается многопоточность

In [247]:
lda.log_perplexity(corpus, total_docs=100)

-97.24543934252829

In [248]:
coherence_model_lda = gensim.models.CoherenceModel(model=lda, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [249]:
topics = []
for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

In [250]:
coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [251]:
coherence_model_lda.get_coherence()

0.4537598623763124

In [267]:
one, two, three = topics[88], topics[64], topics[39]

In [274]:
topics_df_idf = pd.DataFrame([one, two, three], index=['тема1', 'тема2', 'тема3'])

In [275]:
topics_df_idf

0         1           2          3        4       5  \
тема1  заболевание   пациент        врач    лечение      вич  протез   
тема2    вселенная  анимация   галактика  квантовый  батарея  теория   
тема3       клиент      сеть  устройство     сервис  продукт  бизнес   

               6          7         8         9  
тема1  лекарство   иммунный  препарат     кровь  
тема2   рассылка    энергия    звонок  ценность  
тема3     google  мобильный      сайт     рынок

С tf-idf лучше значение перплексии, но хуже -- когерентности. В целом, предобработка текста и обучение на лучших параметрах (`eta='auto', num_topics=100, passes=25`) дают больше хороших распределенний (в топ-10 слов входят более близкие к той или иной теме слова), чем tf-idf. 

### Разложение матриц в sklearn

In [288]:
stexts = [' '.join(text) for text in texts]

In [289]:
vectorizer = TfidfVectorizer(max_features=25000, min_df=5, max_df=0.3)
X = vectorizer.fit_transform(stexts)

In [290]:
model = NMF(n_components=30)

In [291]:
model.fit(X)

NMF(alpha=0.0, beta_loss='frobenius', init=None, l1_ratio=0.0, max_iter=200,
  n_components=30, random_state=None, shuffle=False, solver='cd',
  tol=0.0001, verbose=0)

In [292]:
def get_nmf_topics(model, n_top_words):
    
    #id слов.
    feat_names = vectorizer.get_feature_names()
    
    word_dict = {};
    for i in range(30):
        
        #топ n слов для темы.
        words_ids = model.components_[i].argsort()[:-n_top_words - 1:-1]
        words = [feat_names[key] for key in words_ids]
        word_dict['Topic # ' + '{:02d}'.format(i+1)] = words;
    
    return pd.DataFrame(word_dict);

In [293]:
get_nmf_topics(model, 10)

Topic # 01 Topic # 02 Topic # 03   Topic # 04 Topic # 05  Topic # 06  \
0     бизнес     public       игра       объект       сеть         css   
1    продукт     string      игрок     значение     трафик          js   
2  сотрудник         if    игровой      элемент   интернет  javascript   
3     клиент       void     играть         блок      связь       react   
4     деньги        int         vr     алгоритм   оператор     angular   
5      рынок     return   персонаж        метод         ip         веб   
6   заказчик        new      unity        точка        dpi         vue   
7        crm       null      steam       строка     доступ        html   
8   менеджер      class     движок  изображение    абонент     браузер   
9    продажа        amp       жанр     текстура      канал          es   

   Topic # 07 Topic # 08   Topic # 09     Topic # 10     ...       \
0     android       this  космический          атака     ...        
1      google      react      спутник   безопасность     ...        
2         ios        div       орбита     уязвимость     ...        
3   мобильный      props       ракета  злоумышленник     ...        
4         app  компонент         марс         пароль     ...        
5  устройство   function      аппарат         защита     ...        
6      layout      const      планета    вредоносный     ...        
7       swift     return        земля     устройство     ...        
8        play        dom         луна           ключ     ...        
9        view      class      станция         доступ     ...        

     Topic # 21      Topic # 22  Topic # 23 Topic # 24   Topic # 25  \
0        печать           центр         бот       сайт       камера   
1       принтер            дата    telegram    реклама        видео   
2        станок        облачный   сообщение   страница           vr   
3            мм  инфраструктура         bot     клиент     движение   
4      материал          услуга         чат    контент  регистратор   
5      печатать          облако         api     google   реальность   
6  производство             цод     message    браузер     blackvue   
7        деталь    оборудование  мессенджер  рекламный         кадр   
8       изделие          сервис      телегр      домен      ivideon   
9        модель       провайдер       канал     письмо  виртуальный   

  Topic # 26        Topic # 27     Topic # 28  Topic # 29   Topic # 30  
0       звук              язык             ия       товар   устройство  
1     сигнал  программирование       обучение      скидка     смартфон  
2  усилитель       программист      нейросеть     магазин  аккумулятор  
3    частота            лекция          робот        цена    процессор  
4    наушник              java      интеллект  распродажа      ноутбук  
5     музыка         программа  искусственный  покупатель          usb  
6   звуковой           перевод       машинный     покупка      дисплей  
7  искажение            python      нейронный     пятница      телефон  
8   акустика              курс           сеть      amazon        плата  
9   наушники           ребенок       deepmind       акция        intel  

[10 rows x 30 columns]

In [294]:
# Frobenius norm of the matrix difference, or beta-divergence, 
# between the training data X and the reconstructed data WH from the fitted model.
model.reconstruction_err_

60.468078326398626

**Возьмем другие параметры для TfidfVectorizer**

In [295]:
nvectorizer = TfidfVectorizer(max_features=10000, min_df=5, max_df=0.5)
nX = nvectorizer.fit_transform(stexts)

In [296]:
nmodel = NMF(n_components=30)

In [297]:
nmodel.fit(nX)

NMF(alpha=0.0, beta_loss='frobenius', init=None, l1_ratio=0.0, max_iter=200,
  n_components=30, random_state=None, shuffle=False, solver='cd',
  tol=0.0001, verbose=0)

In [299]:
# Frobenius norm of the matrix difference, or beta-divergence, 
# between the training data X and the reconstructed data WH from the fitted model.
nmodel.reconstruction_err_

59.63358836171295

In [301]:
nvectorizer = TfidfVectorizer(max_features=20000, min_df=5, max_df=0.5)
nX = nvectorizer.fit_transform(stexts)
nmodel = NMF(n_components=30)
nmodel.fit(nX)
nmodel.reconstruction_err_

60.07823547059315

In [302]:
nvectorizer = TfidfVectorizer(max_features=30000, min_df=5, max_df=0.3)
nX = nvectorizer.fit_transform(stexts)
nmodel = NMF(n_components=30)
nmodel.fit(nX)
nmodel.reconstruction_err_

60.46904845083347

In [303]:
get_nmf_topics(nmodel, 10)

Topic # 01 Topic # 02 Topic # 03   Topic # 04 Topic # 05 Topic # 06  \
0       продукт       this       игра       объект        php       файл   
1        клиент      react      игрок     значение       http      папка   
2     сотрудник        div    игровой      элемент     docker     скрипт   
3        бизнес      props     играть     текстура         id     строка   
4      менеджер  компонент         vr     алгоритм       user      пакет   
5      заказчик   function   персонаж         блок     сервер        git   
6           crm      const      unity        метод       name       file   
7   программист     return      steam  изображение      nginx  настройка   
8          опыт        dom     движок        точка     запрос     модуль   
9  тестирование      class       жанр       модель        etc  программа   

   Topic # 07  Topic # 08   Topic # 09     Topic # 10     ...      \
0       товар         css  космический          атака     ...       
1      скидка          js      спутник   безопасность     ...       
2     магазин  javascript       орбита     уязвимость     ...       
3        цена       react       ракета     устройство     ...       
4  распродажа     angular         марс  злоумышленник     ...       
5  покупатель         веб      аппарат         защита     ...       
6     пятница         vue      планета         пароль     ...       
7     покупка        html        земля    вредоносный     ...       
8       заказ     браузер         луна           сеть     ...       
9     продажа          es      станция         доступ     ...       

     Topic # 21 Topic # 22  Topic # 23  Topic # 24 Topic # 25  Topic # 26  \
0        печать     public         бот     android       сайт      сигнал   
1       принтер       void    telegram      google    реклама        звук   
2        станок     string   сообщение         ios   страница     частота   
3            мм        new         bot   мобильный    контент   усилитель   
4      материал      class         чат  устройство    браузер   искажение   
5      печатать      класс         api         app      домен     наушник   
6  производство    private     message      layout     клиент    звуковой   
7        деталь     return  мессенджер       swift  рекламный        сеть   
8       изделие      метод       канал        play     google  устройство   
9        металл        var      телегр        view     трафик      музыка   

    Topic # 27 Topic # 28      Topic # 29  Topic # 30  
0       камера         if           центр  российский  
1   устройство        int            дата      страна  
2     смартфон        amp  инфраструктура      россия  
3      телефон     return          услуга       налог  
4  аккумулятор        std        облачный       рубль  
5      дисплей      count          облако       закон  
6        видео      const    оборудование       рынок  
7        экран       null          сервер       доход  
8       датчик       char          сервис   налоговый  
9       xiaomi       else             цод         ооо  

[10 rows x 30 columns]

**Таким образом**, мы получили хорошие результаты как с `LDA`, так и с `NMF`. Но кажется, что результаты `NMF` позволяют нам в большем числе случаев (посравнению с `LDA`) однозачно определить тему.